In [30]:
import numpy as np
import matplotlib.pyplot as plt
from matplotlib.patches import Polygon
import sys
''' Script to weave a swatch of weft-facing 2/2 twill,
    representing the weft as a sequence of lozenges
    straddling two adjacent warps.
    Treats straight and broken twills separately:
    toggle using "Broken = False/True"
    Set up the loom and choose colours (<=4) and colour sequence by editing
    lines of code between ###...###
    
    See ch. 7 of "Techniques of Rug Weaving" by
    Peter Collingwood (Faber & Faber ISBN 0-571-16994-5)'''

nwarps = 40    #  width of swatch
nwefts = 240    #  length of swatch

pitch = 0.6      #  weft spacing : warp spacing
pon2 = pitch/2   #  alternate wefts for broken twill spaced halfway inbetween
pon4 = pitch/4   #  quarter spacing needed for straight twill..

Broken = True    #  choose False for straight twill, True for broken....

nshafts = 4                              # number of shafts
tieups = [(0,3),(0,1),(1,2),(2,3)]       # action of treadles   (top right of draft)
shaft = [0,1,2,3]                        # threading stencil (top of draft)
warp_repeat = len(shaft)

if Broken:
    treadle = [1,2,0,3]                  # treadling stencil (RH of draft)
else:
    treadle = [1,2,3,0]
weft_repeat = len(treadle)

###################################################################################
''' this function arranges up to four strings in a sequence of arbitrary length.
    For best results choose letters to respect alphabetical ordering'''
def sequence(A,B,C,D):
    return [A,B,C,C,C,A,B]         # shuttle colour sequence

'''dictionary of available colours and their corresponding shadows (to enhance appearance)
   add further colours as required - find RGB hex codes using eg. Keynote colour tool'''
colour = {'red': '#ff0000',           'dred': '#660000',\
          'blue': '#0000ff',          'dblue': '#000066',\
          'yellow': '#ffff00',        'dyellow': '#bbbb00',\
          'green': '#00dd00',         'dgreen': '#006600',\
          'pale_blue': '#2daae7',     'dpale_blue': '#222266',\
          'dark_blue': '#000066',     'ddark_blue': '#000044',\
          'orange': '#ff4400',        'dorange': '#662200',\
          'salmon_pink': '#DC7F5F',   'dsalmon_pink': '#8C3F1F',\
          'navy_blue': '#181138',     'dnavy_blue': '#000000',\
          'pink': '#efadbc',          'dpink': '#af2f77',\
          'purple': '#9426E5',        'dpurple': '#6400BD',\
          'dark_purple': '#6400bd',   'ddark_purple': '#6400BD',\
          'shocking_pink': '#EF2F9C', 'dshocking_pink': '#67279C',\
          'turquoise':  '#0bc0c1',    'dturquoise': '#000066'
}

c = ['blue','red','yellow','pale_blue']  # choose at least 4 colours in order by editing this line
d = 'd'+' d'.join(c)
dc = d.split()

shuttle = sequence(colour[c[0]],colour[c[1]],colour[c[2]],colour[c[3]])
shadow  = sequence(colour[dc[0]],colour[dc[1]],colour[dc[2]],colour[dc[3]])

letter_label = ['A: ','  B: ','  C: ','  D: ',]

col_repeat = len(shuttle)
##################################################################################

x = np.linspace(1,nwarps+2,nwarps+2)     # define physical coordinates with warp spacing = 1.0

# ...thread the heddles...
heddle = np.zeros((nwarps+2,nshafts),dtype='b')
for i in range(len(x)):
    heddle[i,shaft[i%warp_repeat]] = True

# ...tie up to give a shed for each treadle...
first_shed = True
for tieup in tieups:
    p = np.zeros(nwarps+2,dtype='b')
    for sh in tieup:
        p += heddle[:,sh]
    if first_shed:
        shed = p
        first_shed = False
    else:
        shed = np.vstack((shed, p))

fig = plt.figure(edgecolor='w')
ax = fig.add_subplot(111,aspect='equal')

y = np.zeros(nwarps,dtype='f')           # vertical destination of weft

'''these conditions ensure the weave is correctly represented in the figure,
   so that later wefts lie above previous ones'''
if Broken:                 # 2 picks per pitch
    pup, pdown = pon2, pon2
    for i in range(nwarps):
        if i%2:            # positions alternate wefts correctly after beating down
           y[i] += pon2
        if not(i-2)%4:     # correction so later wefts lie above earlier ones
           y[i] += pitch
else:                      # 4 picks per pitch
    pup, pdown = (pon2+pon4), (pon2-pon4)
    for i in range(nwarps):
        if i%2:            # positions alternate wefts correctly after beating down
            y[i] += pon4
        if not(i-2)%4:     # correction so later wefts lie above earlier ones
            y[i] += pon2
        if not(i-3)%4:     # further correction so later wefts lie above earlier ones
            y[i] += pon2

# ... and we're off!
for j in range(nwefts):    # loop on throwing the shuttle
    for i in range(nwarps):
        if  shed[treadle[j%weft_repeat],i] and \
            shed[treadle[j%weft_repeat],i+1]:  # checks shed for adjacent down warps => weft on top
                weft = Polygon(((x[i],y[i]+pup),(x[i+1],y[i]+pitch),\
                                (x[i+2],y[i]+pdown),(x[i+1],y[i])),\
                            fc=shuttle[j%col_repeat],ec=shadow[j%col_repeat])
                y[i] += pitch                  # set vertical postion of next weft
                
                ax.add_artist(weft)

title = sequence('A','B','C','D')
letter_max = 'A'
seq = ''
for letter in title:
    seq += letter
    if letter > letter_max:
        letter_max = letter
ax.set_xlim(1,nwarps+2)
if Broken:
    ax.set_ylim(0,pitch*(nwefts+4)/4)
    style = 'Broken Twill'
else:
    ax.set_ylim(-pitch,pitch*(nwefts+6)/4)
    style = 'Straight Twill'
fig.suptitle('{}:    {}'.format(style,seq))  # Print weave and colour sequence in title

label = ''
last_letter = ''
i = 0
for letter in title:
    if letter > last_letter:
        label += letter_label[i]+c[i]
        last_letter = letter
        if letter == letter_max:
            break
        i += 1
prettylabel = ''                       # prettylabel has underscores replaced by spaces
for letter in label:
    if letter == '_':
         prettylabel += ' '
    else:
         prettylabel += letter
ax.set_xlabel(prettylabel)                         # Print colour key below x-axis

ax.set_xticks([])
ax.yaxis.set_visible(False)

plt.savefig('rug.png',dpi=300)